In [40]:
import cv2
import numpy as np
import os
import scipy.io as sio
import torch
import torchvision.transforms as transforms
import torchvision.models as models
import torch.nn as nn
import csv
import time
import pickle

In [41]:
# Device configuration
if torch.cuda.is_available():
    print("GPU is active")
    device = torch.device('cuda')
else:
    device = torch.device('cpu')
    
#CSV file reading
"""
Generating dictionaries
for photo_id ---> buisness_id
"""
photo_to_bus_dict = {}
with open('train_photo_to_biz_ids.csv') as csv_file:
    csv_reader = csv.reader(csv_file, delimiter=',')
    line_count = 0
    for row in csv_reader:
        if line_count == 0:
            print(f'Column names are {", ".join(row)}')
            line_count += 1
        else:
            photo_to_bus_dict[row[0]] = row[1]
#             print(f'\t{row[0]} works in the {row[1]} department')
            line_count += 1
    print(f'Processed {line_count} lines.')
print(len(photo_to_bus_dict))
    
"""
Generating dictionaries
for business_id ---> labels
"""
bus_to_labels_dict = {}     
with open('train.csv') as csv_file:
    csv_reader = csv.reader(csv_file, delimiter=',')
    line_count = 0
    for row in csv_reader:
        if line_count == 0:
            print(f'Column names are {", ".join(row)}')
            line_count += 1
        else:
            bus_to_labels_dict[row[0]] = [row[1]]
#             print(f'\t{row[0]} works in the {row[1]} department')
            line_count += 1
    print(f'Processed {line_count} lines.')  
print(len(bus_to_labels_dict))

"""
Creates no_images*labels_size matrix
with each row indicating what labels
are assigned to each photo
"""
def id_to_label(photo_ids):
    photo_labels = np.empty(shape=[0,9])
    for id in photo_ids:
        lst_labels = bus_to_labels_dict[photo_to_bus_dict[id]]
        ls = lst_labels[0].split(' ')
        labels = [0]*9
        for label in ls:
            if label !='':
                labels[int(label)] = 1
        labels = np.array(labels).reshape(1,-1)
        photo_labels = np.append(photo_labels,labels,axis=0)
    return photo_labels


GPU is active
Column names are photo_id, business_id
Processed 234843 lines.
234842
Column names are business_id, labels
Processed 2001 lines.
2000


In [42]:
from sklearn import svm
from sklearn.multiclass import OneVsRestClassifier
from sklearn import linear_model

#inputpath = 'gen_data/vgg7avg/'
inputpath = 'gen_data/vgg_resize/'
outpath = 'gen_data/vgg_outputs_app50k_'

random_state = np.random.RandomState(0)
classifier = OneVsRestClassifier(svm.SVC(kernel='linear', C=1.0, probability=True, random_state=random_state, 
                                        max_iter = 10))
classifier_sgd = OneVsRestClassifier(linear_model.SGDClassifier(max_iter=10, tol=1e-3))
    
i = 1
file_list = sorted(os.listdir(inputpath))
train_list = file_list[:54000]
np_data = np.empty(shape=[0, 4096])
np_label = np.empty(shape=[0,9])

for file_name in train_list:
    print(file_name, '-', i)
    data = sio.loadmat(inputpath + file_name)
    data = data['features']
    #print(data.shape)
    f = file_name.split('.')
    label = id_to_label([f[0]])
    label = label.reshape((-1, 9))
    
    #classifier_sgd.partial_fit(data, label, classes=2)
    np_data = np.append(np_data, data, axis = 0)
    np_label = np.append(np_label, label, axis = 0)
    
    #print(label, label.shape)
    #break
    i = i + 1
 
#sio.savemat(outpath + 'data' + '.vgg', {'data':np_data}, do_compression=True)
#sio.savemat(outpath + 'label' + '.vgg', {'label':np_label}, do_compression=True)

#classifier.fit(np_data, np_label)    
    

10.jpg.vgg.mat - 1
100009.jpg.vgg.mat - 2
100021.jpg.vgg.mat - 3
100032.jpg.vgg.mat - 4
100034.jpg.vgg.mat - 5
100036.jpg.vgg.mat - 6
100039.jpg.vgg.mat - 7
10004.jpg.vgg.mat - 8
100043.jpg.vgg.mat - 9
100048.jpg.vgg.mat - 10
100061.jpg.vgg.mat - 11
100073.jpg.vgg.mat - 12
100087.jpg.vgg.mat - 13
100088.jpg.vgg.mat - 14
10009.jpg.vgg.mat - 15
100093.jpg.vgg.mat - 16
100097.jpg.vgg.mat - 17
1001.jpg.vgg.mat - 18
100100.jpg.vgg.mat - 19
100101.jpg.vgg.mat - 20
100105.jpg.vgg.mat - 21
100113.jpg.vgg.mat - 22
100135.jpg.vgg.mat - 23
10014.jpg.vgg.mat - 24
100147.jpg.vgg.mat - 25
10016.jpg.vgg.mat - 26
100163.jpg.vgg.mat - 27
100168.jpg.vgg.mat - 28
100179.jpg.vgg.mat - 29
100180.jpg.vgg.mat - 30
100181.jpg.vgg.mat - 31
100184.jpg.vgg.mat - 32
100185.jpg.vgg.mat - 33
1002.jpg.vgg.mat - 34
100206.jpg.vgg.mat - 35
100209.jpg.vgg.mat - 36
10022.jpg.vgg.mat - 37
100223.jpg.vgg.mat - 38
10023.jpg.vgg.mat - 39
100233.jpg.vgg.mat - 40
100235.jpg.vgg.mat - 41
100237.jpg.vgg.mat - 42
100239.jpg.vgg.

102120.jpg.vgg.mat - 364
102127.jpg.vgg.mat - 365
102128.jpg.vgg.mat - 366
102130.jpg.vgg.mat - 367
102131.jpg.vgg.mat - 368
102134.jpg.vgg.mat - 369
102138.jpg.vgg.mat - 370
102140.jpg.vgg.mat - 371
102149.jpg.vgg.mat - 372
102151.jpg.vgg.mat - 373
102154.jpg.vgg.mat - 374
10216.jpg.vgg.mat - 375
102170.jpg.vgg.mat - 376
102171.jpg.vgg.mat - 377
102176.jpg.vgg.mat - 378
10218.jpg.vgg.mat - 379
102180.jpg.vgg.mat - 380
102187.jpg.vgg.mat - 381
102188.jpg.vgg.mat - 382
102193.jpg.vgg.mat - 383
102199.jpg.vgg.mat - 384
102202.jpg.vgg.mat - 385
102203.jpg.vgg.mat - 386
102206.jpg.vgg.mat - 387
102210.jpg.vgg.mat - 388
102211.jpg.vgg.mat - 389
102213.jpg.vgg.mat - 390
102224.jpg.vgg.mat - 391
102227.jpg.vgg.mat - 392
102229.jpg.vgg.mat - 393
10223.jpg.vgg.mat - 394
102237.jpg.vgg.mat - 395
102249.jpg.vgg.mat - 396
102251.jpg.vgg.mat - 397
102256.jpg.vgg.mat - 398
102260.jpg.vgg.mat - 399
102269.jpg.vgg.mat - 400
102282.jpg.vgg.mat - 401
102298.jpg.vgg.mat - 402
102302.jpg.vgg.mat - 403
102

10418.jpg.vgg.mat - 718
104189.jpg.vgg.mat - 719
104192.jpg.vgg.mat - 720
104196.jpg.vgg.mat - 721
104205.jpg.vgg.mat - 722
104206.jpg.vgg.mat - 723
104208.jpg.vgg.mat - 724
104216.jpg.vgg.mat - 725
10422.jpg.vgg.mat - 726
104223.jpg.vgg.mat - 727
104228.jpg.vgg.mat - 728
104242.jpg.vgg.mat - 729
104254.jpg.vgg.mat - 730
104255.jpg.vgg.mat - 731
104262.jpg.vgg.mat - 732
104275.jpg.vgg.mat - 733
104277.jpg.vgg.mat - 734
104279.jpg.vgg.mat - 735
104285.jpg.vgg.mat - 736
104288.jpg.vgg.mat - 737
104291.jpg.vgg.mat - 738
104297.jpg.vgg.mat - 739
104313.jpg.vgg.mat - 740
104327.jpg.vgg.mat - 741
104331.jpg.vgg.mat - 742
104333.jpg.vgg.mat - 743
104336.jpg.vgg.mat - 744
104340.jpg.vgg.mat - 745
104348.jpg.vgg.mat - 746
104350.jpg.vgg.mat - 747
104354.jpg.vgg.mat - 748
104356.jpg.vgg.mat - 749
104357.jpg.vgg.mat - 750
104365.jpg.vgg.mat - 751
104366.jpg.vgg.mat - 752
104378.jpg.vgg.mat - 753
104387.jpg.vgg.mat - 754
104394.jpg.vgg.mat - 755
104398.jpg.vgg.mat - 756
104399.jpg.vgg.mat - 757
10

106082.jpg.vgg.mat - 1071
106094.jpg.vgg.mat - 1072
106107.jpg.vgg.mat - 1073
106110.jpg.vgg.mat - 1074
106117.jpg.vgg.mat - 1075
106119.jpg.vgg.mat - 1076
106120.jpg.vgg.mat - 1077
106125.jpg.vgg.mat - 1078
106126.jpg.vgg.mat - 1079
106134.jpg.vgg.mat - 1080
106135.jpg.vgg.mat - 1081
106136.jpg.vgg.mat - 1082
106140.jpg.vgg.mat - 1083
106145.jpg.vgg.mat - 1084
106146.jpg.vgg.mat - 1085
106147.jpg.vgg.mat - 1086
106148.jpg.vgg.mat - 1087
106153.jpg.vgg.mat - 1088
106164.jpg.vgg.mat - 1089
106170.jpg.vgg.mat - 1090
106171.jpg.vgg.mat - 1091
106173.jpg.vgg.mat - 1092
106185.jpg.vgg.mat - 1093
106186.jpg.vgg.mat - 1094
10620.jpg.vgg.mat - 1095
106201.jpg.vgg.mat - 1096
106211.jpg.vgg.mat - 1097
106213.jpg.vgg.mat - 1098
106214.jpg.vgg.mat - 1099
106218.jpg.vgg.mat - 1100
106227.jpg.vgg.mat - 1101
106232.jpg.vgg.mat - 1102
106237.jpg.vgg.mat - 1103
106240.jpg.vgg.mat - 1104
106247.jpg.vgg.mat - 1105
106257.jpg.vgg.mat - 1106
106270.jpg.vgg.mat - 1107
106286.jpg.vgg.mat - 1108
106289.jpg.vg

10793.jpg.vgg.mat - 1393
107931.jpg.vgg.mat - 1394
107936.jpg.vgg.mat - 1395
107938.jpg.vgg.mat - 1396
10794.jpg.vgg.mat - 1397
107955.jpg.vgg.mat - 1398
107956.jpg.vgg.mat - 1399
107957.jpg.vgg.mat - 1400
107967.jpg.vgg.mat - 1401
10797.jpg.vgg.mat - 1402
107970.jpg.vgg.mat - 1403
107972.jpg.vgg.mat - 1404
107978.jpg.vgg.mat - 1405
107979.jpg.vgg.mat - 1406
10798.jpg.vgg.mat - 1407
107983.jpg.vgg.mat - 1408
107992.jpg.vgg.mat - 1409
107999.jpg.vgg.mat - 1410
10801.jpg.vgg.mat - 1411
108012.jpg.vgg.mat - 1412
10802.jpg.vgg.mat - 1413
108022.jpg.vgg.mat - 1414
108023.jpg.vgg.mat - 1415
108026.jpg.vgg.mat - 1416
10803.jpg.vgg.mat - 1417
108030.jpg.vgg.mat - 1418
108031.jpg.vgg.mat - 1419
108049.jpg.vgg.mat - 1420
108061.jpg.vgg.mat - 1421
108064.jpg.vgg.mat - 1422
108067.jpg.vgg.mat - 1423
108070.jpg.vgg.mat - 1424
108085.jpg.vgg.mat - 1425
108091.jpg.vgg.mat - 1426
108094.jpg.vgg.mat - 1427
108097.jpg.vgg.mat - 1428
10810.jpg.vgg.mat - 1429
108106.jpg.vgg.mat - 1430
108112.jpg.vgg.mat -

...

401595.jpg.vgg.mat - 52493
401601.jpg.vgg.mat - 52494
401604.jpg.vgg.mat - 52495
401609.jpg.vgg.mat - 52496
401610.jpg.vgg.mat - 52497
401615.jpg.vgg.mat - 52498
401618.jpg.vgg.mat - 52499
401639.jpg.vgg.mat - 52500
401643.jpg.vgg.mat - 52501
401674.jpg.vgg.mat - 52502
401690.jpg.vgg.mat - 52503
401691.jpg.vgg.mat - 52504
401694.jpg.vgg.mat - 52505
401698.jpg.vgg.mat - 52506
401705.jpg.vgg.mat - 52507
401708.jpg.vgg.mat - 52508
401712.jpg.vgg.mat - 52509
401714.jpg.vgg.mat - 52510
401715.jpg.vgg.mat - 52511
401727.jpg.vgg.mat - 52512
401739.jpg.vgg.mat - 52513
401746.jpg.vgg.mat - 52514
40175.jpg.vgg.mat - 52515
401751.jpg.vgg.mat - 52516
401753.jpg.vgg.mat - 52517
401757.jpg.vgg.mat - 52518
401758.jpg.vgg.mat - 52519
401762.jpg.vgg.mat - 52520
401769.jpg.vgg.mat - 52521
401774.jpg.vgg.mat - 52522
401786.jpg.vgg.mat - 52523
401789.jpg.vgg.mat - 52524
401800.jpg.vgg.mat - 52525
401801.jpg.vgg.mat - 52526
401802.jpg.vgg.mat - 52527
401814.jpg.vgg.mat - 52528
401823.jpg.vgg.mat - 52529
40

403624.jpg.vgg.mat - 52798
403629.jpg.vgg.mat - 52799
403634.jpg.vgg.mat - 52800
403638.jpg.vgg.mat - 52801
403641.jpg.vgg.mat - 52802
403643.jpg.vgg.mat - 52803
403661.jpg.vgg.mat - 52804
403664.jpg.vgg.mat - 52805
403676.jpg.vgg.mat - 52806
40368.jpg.vgg.mat - 52807
403681.jpg.vgg.mat - 52808
403689.jpg.vgg.mat - 52809
403694.jpg.vgg.mat - 52810
403697.jpg.vgg.mat - 52811
403699.jpg.vgg.mat - 52812
4037.jpg.vgg.mat - 52813
403718.jpg.vgg.mat - 52814
403719.jpg.vgg.mat - 52815
403726.jpg.vgg.mat - 52816
403727.jpg.vgg.mat - 52817
403735.jpg.vgg.mat - 52818
403739.jpg.vgg.mat - 52819
403740.jpg.vgg.mat - 52820
403742.jpg.vgg.mat - 52821
403746.jpg.vgg.mat - 52822
403755.jpg.vgg.mat - 52823
40376.jpg.vgg.mat - 52824
403761.jpg.vgg.mat - 52825
403769.jpg.vgg.mat - 52826
403781.jpg.vgg.mat - 52827
403782.jpg.vgg.mat - 52828
40379.jpg.vgg.mat - 52829
403798.jpg.vgg.mat - 52830
4038.jpg.vgg.mat - 52831
403805.jpg.vgg.mat - 52832
403806.jpg.vgg.mat - 52833
403810.jpg.vgg.mat - 52834
403812.j

405376.jpg.vgg.mat - 53103
405378.jpg.vgg.mat - 53104
405381.jpg.vgg.mat - 53105
405395.jpg.vgg.mat - 53106
405397.jpg.vgg.mat - 53107
405404.jpg.vgg.mat - 53108
405419.jpg.vgg.mat - 53109
40542.jpg.vgg.mat - 53110
405429.jpg.vgg.mat - 53111
405431.jpg.vgg.mat - 53112
405433.jpg.vgg.mat - 53113
405437.jpg.vgg.mat - 53114
40544.jpg.vgg.mat - 53115
405448.jpg.vgg.mat - 53116
405452.jpg.vgg.mat - 53117
405453.jpg.vgg.mat - 53118
405466.jpg.vgg.mat - 53119
405476.jpg.vgg.mat - 53120
405487.jpg.vgg.mat - 53121
405498.jpg.vgg.mat - 53122
405500.jpg.vgg.mat - 53123
405502.jpg.vgg.mat - 53124
405522.jpg.vgg.mat - 53125
405536.jpg.vgg.mat - 53126
405558.jpg.vgg.mat - 53127
40556.jpg.vgg.mat - 53128
405567.jpg.vgg.mat - 53129
405569.jpg.vgg.mat - 53130
405571.jpg.vgg.mat - 53131
405572.jpg.vgg.mat - 53132
405577.jpg.vgg.mat - 53133
405578.jpg.vgg.mat - 53134
405586.jpg.vgg.mat - 53135
40559.jpg.vgg.mat - 53136
4056.jpg.vgg.mat - 53137
405603.jpg.vgg.mat - 53138
405617.jpg.vgg.mat - 53139
405619.

407251.jpg.vgg.mat - 53408
407254.jpg.vgg.mat - 53409
407255.jpg.vgg.mat - 53410
407258.jpg.vgg.mat - 53411
407275.jpg.vgg.mat - 53412
407289.jpg.vgg.mat - 53413
407290.jpg.vgg.mat - 53414
407301.jpg.vgg.mat - 53415
407303.jpg.vgg.mat - 53416
407307.jpg.vgg.mat - 53417
407308.jpg.vgg.mat - 53418
407312.jpg.vgg.mat - 53419
407322.jpg.vgg.mat - 53420
407325.jpg.vgg.mat - 53421
407336.jpg.vgg.mat - 53422
40734.jpg.vgg.mat - 53423
407340.jpg.vgg.mat - 53424
407349.jpg.vgg.mat - 53425
407356.jpg.vgg.mat - 53426
407361.jpg.vgg.mat - 53427
407366.jpg.vgg.mat - 53428
40738.jpg.vgg.mat - 53429
407385.jpg.vgg.mat - 53430
407389.jpg.vgg.mat - 53431
407390.jpg.vgg.mat - 53432
407391.jpg.vgg.mat - 53433
407399.jpg.vgg.mat - 53434
407403.jpg.vgg.mat - 53435
407410.jpg.vgg.mat - 53436
407418.jpg.vgg.mat - 53437
407425.jpg.vgg.mat - 53438
407426.jpg.vgg.mat - 53439
407429.jpg.vgg.mat - 53440
40743.jpg.vgg.mat - 53441
407434.jpg.vgg.mat - 53442
407439.jpg.vgg.mat - 53443
407443.jpg.vgg.mat - 53444
4074

409004.jpg.vgg.mat - 53713
409012.jpg.vgg.mat - 53714
409021.jpg.vgg.mat - 53715
409030.jpg.vgg.mat - 53716
409031.jpg.vgg.mat - 53717
409040.jpg.vgg.mat - 53718
409045.jpg.vgg.mat - 53719
409053.jpg.vgg.mat - 53720
409055.jpg.vgg.mat - 53721
409064.jpg.vgg.mat - 53722
409068.jpg.vgg.mat - 53723
409076.jpg.vgg.mat - 53724
409095.jpg.vgg.mat - 53725
409096.jpg.vgg.mat - 53726
409100.jpg.vgg.mat - 53727
409105.jpg.vgg.mat - 53728
409107.jpg.vgg.mat - 53729
409112.jpg.vgg.mat - 53730
409117.jpg.vgg.mat - 53731
409123.jpg.vgg.mat - 53732
409145.jpg.vgg.mat - 53733
409146.jpg.vgg.mat - 53734
409147.jpg.vgg.mat - 53735
409153.jpg.vgg.mat - 53736
409172.jpg.vgg.mat - 53737
40918.jpg.vgg.mat - 53738
409187.jpg.vgg.mat - 53739
409188.jpg.vgg.mat - 53740
409194.jpg.vgg.mat - 53741
409198.jpg.vgg.mat - 53742
409204.jpg.vgg.mat - 53743
409205.jpg.vgg.mat - 53744
409207.jpg.vgg.mat - 53745
409213.jpg.vgg.mat - 53746
409220.jpg.vgg.mat - 53747
409222.jpg.vgg.mat - 53748
409226.jpg.vgg.mat - 53749
40

In [55]:
"""
np_data = sio.loadmat('gen_data/vgg_outputs_10k_data.vgg')
np_data = np_data['data']
np_label = sio.loadmat('gen_data/vgg_outputs_10k_label.vgg')
np_label = np_label['label']
"""

classifier_2 = OneVsRestClassifier(svm.SVC(kernel='linear', C=1.0, probability=True, random_state=random_state, 
                                        max_iter = 100))

print("Training start")
t1 = time.time()
classifier_2.fit(np_data, np_label)
print("Training done")
print("Training time for 50000 images took %0.3fs." % (time.time() - t1))


Training start


/home/pmadugundu/anaconda3/lib/python3.7/site-packages/sklearn/svm/base.py:218: ConvergenceWarning: Solver terminated early (max_iter=100).  Consider pre-processing your data with StandardScaler or MinMaxScaler.
  % self.max_iter, ConvergenceWarning)
/home/pmadugundu/anaconda3/lib/python3.7/site-packages/sklearn/svm/base.py:218: ConvergenceWarning: Solver terminated early (max_iter=100).  Consider pre-processing your data with StandardScaler or MinMaxScaler.
  % self.max_iter, ConvergenceWarning)
/home/pmadugundu/anaconda3/lib/python3.7/site-packages/sklearn/svm/base.py:218: ConvergenceWarning: Solver terminated early (max_iter=100).  Consider pre-processing your data with StandardScaler or MinMaxScaler.
  % self.max_iter, ConvergenceWarning)
/home/pmadugundu/anaconda3/lib/python3.7/site-packages/sklearn/svm/base.py:218: ConvergenceWarning: Solver terminated early (max_iter=100).  Consider pre-processing your data with StandardScaler or MinMaxScaler.
  % self.max_iter, ConvergenceWarni

Training done
Training time for 50000 images took 3711.993s.


/home/pmadugundu/anaconda3/lib/python3.7/site-packages/sklearn/svm/base.py:218: ConvergenceWarning: Solver terminated early (max_iter=100).  Consider pre-processing your data with StandardScaler or MinMaxScaler.
  % self.max_iter, ConvergenceWarning)


In [43]:
from sklearn.multioutput import MultiOutputClassifier 
from sklearn.svm import LinearSVC
"""
np_data = sio.loadmat('gen_data/vgg_outputs_10k_data.vgg')
np_data = np_data['data']
np_label = sio.loadmat('gen_data/vgg_outputs_10k_label.vgg')
np_label = np_label['label']
"""

print("Training start")
t1 = time.time()
classifier_3 = MultiOutputClassifier(LinearSVC(random_state=0, max_iter=100))
classifier_3.fit(np_data, np_label)

print("Training done")
print("Training time of MultiOutputClassifier for 50000 images took %0.3fs." % (time.time() - t1))

Training start
Training done
Training time of MultiOutputClassifier for 50000 images took 636.348s.


In [51]:
### testing the model
inputpath = 'gen_data/correct_test/vgg_resize/'

test_list = sorted(os.listdir(inputpath))
pred_list = []
label_list = []
i = 1
for file_name in test_list:
    print(file_name, '-', i)
    data = sio.loadmat(inputpath + file_name)
    data = data['features']
    #print(data.shape)
    f = file_name.split('.')
    label = id_to_label([f[0]])
    label = label.reshape((-1, 9))
    #print(label)
    #break
    pred = classifier_3.predict(data)
    i = i + 1
    label_list.append(label)
    pred_list.append(pred)

10.jpg.vgg.mat - 1
100009.jpg.vgg.mat - 2
100021.jpg.vgg.mat - 3
100032.jpg.vgg.mat - 4
100034.jpg.vgg.mat - 5
100036.jpg.vgg.mat - 6
100039.jpg.vgg.mat - 7
10004.jpg.vgg.mat - 8
100043.jpg.vgg.mat - 9
100048.jpg.vgg.mat - 10
100061.jpg.vgg.mat - 11
100073.jpg.vgg.mat - 12
100087.jpg.vgg.mat - 13
100088.jpg.vgg.mat - 14
10009.jpg.vgg.mat - 15
100093.jpg.vgg.mat - 16
100097.jpg.vgg.mat - 17
1001.jpg.vgg.mat - 18
100100.jpg.vgg.mat - 19
100101.jpg.vgg.mat - 20
100105.jpg.vgg.mat - 21
100113.jpg.vgg.mat - 22
100135.jpg.vgg.mat - 23
10014.jpg.vgg.mat - 24
100147.jpg.vgg.mat - 25
10016.jpg.vgg.mat - 26
100163.jpg.vgg.mat - 27
100168.jpg.vgg.mat - 28
100179.jpg.vgg.mat - 29
100180.jpg.vgg.mat - 30
100181.jpg.vgg.mat - 31
100184.jpg.vgg.mat - 32
100185.jpg.vgg.mat - 33
1002.jpg.vgg.mat - 34
100206.jpg.vgg.mat - 35
100209.jpg.vgg.mat - 36
10022.jpg.vgg.mat - 37
100223.jpg.vgg.mat - 38
10023.jpg.vgg.mat - 39
100233.jpg.vgg.mat - 40
100235.jpg.vgg.mat - 41
100237.jpg.vgg.mat - 42
100239.jpg.vgg.

102418.jpg.vgg.mat - 423
102421.jpg.vgg.mat - 424
102439.jpg.vgg.mat - 425
102440.jpg.vgg.mat - 426
102441.jpg.vgg.mat - 427
102449.jpg.vgg.mat - 428
102450.jpg.vgg.mat - 429
10247.jpg.vgg.mat - 430
102486.jpg.vgg.mat - 431
102493.jpg.vgg.mat - 432
102507.jpg.vgg.mat - 433
102510.jpg.vgg.mat - 434
102515.jpg.vgg.mat - 435
102531.jpg.vgg.mat - 436
102536.jpg.vgg.mat - 437
10254.jpg.vgg.mat - 438
102541.jpg.vgg.mat - 439
102557.jpg.vgg.mat - 440
102564.jpg.vgg.mat - 441
102575.jpg.vgg.mat - 442
102579.jpg.vgg.mat - 443
102589.jpg.vgg.mat - 444
102591.jpg.vgg.mat - 445
102595.jpg.vgg.mat - 446
102604.jpg.vgg.mat - 447
102610.jpg.vgg.mat - 448
102615.jpg.vgg.mat - 449
102618.jpg.vgg.mat - 450
102619.jpg.vgg.mat - 451
102621.jpg.vgg.mat - 452
102627.jpg.vgg.mat - 453
102651.jpg.vgg.mat - 454
102652.jpg.vgg.mat - 455
102662.jpg.vgg.mat - 456
102664.jpg.vgg.mat - 457
102668.jpg.vgg.mat - 458
102676.jpg.vgg.mat - 459
102678.jpg.vgg.mat - 460
10268.jpg.vgg.mat - 461
102685.jpg.vgg.mat - 462
102

104934.jpg.vgg.mat - 859
104937.jpg.vgg.mat - 860
104942.jpg.vgg.mat - 861
104945.jpg.vgg.mat - 862
104949.jpg.vgg.mat - 863
104952.jpg.vgg.mat - 864
104954.jpg.vgg.mat - 865
104956.jpg.vgg.mat - 866
104957.jpg.vgg.mat - 867
104960.jpg.vgg.mat - 868
104962.jpg.vgg.mat - 869
104969.jpg.vgg.mat - 870
104975.jpg.vgg.mat - 871
104978.jpg.vgg.mat - 872
104983.jpg.vgg.mat - 873
104987.jpg.vgg.mat - 874
104994.jpg.vgg.mat - 875
1050.jpg.vgg.mat - 876
105000.jpg.vgg.mat - 877
105009.jpg.vgg.mat - 878
105011.jpg.vgg.mat - 879
105016.jpg.vgg.mat - 880
105019.jpg.vgg.mat - 881
105023.jpg.vgg.mat - 882
105026.jpg.vgg.mat - 883
105028.jpg.vgg.mat - 884
105029.jpg.vgg.mat - 885
105034.jpg.vgg.mat - 886
105044.jpg.vgg.mat - 887
105047.jpg.vgg.mat - 888
10505.jpg.vgg.mat - 889
105057.jpg.vgg.mat - 890
10506.jpg.vgg.mat - 891
105060.jpg.vgg.mat - 892
105069.jpg.vgg.mat - 893
105073.jpg.vgg.mat - 894
105076.jpg.vgg.mat - 895
105085.jpg.vgg.mat - 896
105086.jpg.vgg.mat - 897
105087.jpg.vgg.mat - 898
1050

107219.jpg.vgg.mat - 1274
107225.jpg.vgg.mat - 1275
107233.jpg.vgg.mat - 1276
10724.jpg.vgg.mat - 1277
107240.jpg.vgg.mat - 1278
107243.jpg.vgg.mat - 1279
107244.jpg.vgg.mat - 1280
107245.jpg.vgg.mat - 1281
107246.jpg.vgg.mat - 1282
107251.jpg.vgg.mat - 1283
107254.jpg.vgg.mat - 1284
107255.jpg.vgg.mat - 1285
107266.jpg.vgg.mat - 1286
107270.jpg.vgg.mat - 1287
107275.jpg.vgg.mat - 1288
107277.jpg.vgg.mat - 1289
107288.jpg.vgg.mat - 1290
107293.jpg.vgg.mat - 1291
107296.jpg.vgg.mat - 1292
107297.jpg.vgg.mat - 1293
107307.jpg.vgg.mat - 1294
107311.jpg.vgg.mat - 1295
107319.jpg.vgg.mat - 1296
107321.jpg.vgg.mat - 1297
107323.jpg.vgg.mat - 1298
10733.jpg.vgg.mat - 1299
107330.jpg.vgg.mat - 1300
107347.jpg.vgg.mat - 1301
107353.jpg.vgg.mat - 1302
107376.jpg.vgg.mat - 1303
107392.jpg.vgg.mat - 1304
107408.jpg.vgg.mat - 1305
107426.jpg.vgg.mat - 1306
107435.jpg.vgg.mat - 1307
107439.jpg.vgg.mat - 1308
107446.jpg.vgg.mat - 1309
107455.jpg.vgg.mat - 1310
107457.jpg.vgg.mat - 1311
107458.jpg.vgg

109605.jpg.vgg.mat - 1688
109613.jpg.vgg.mat - 1689
10962.jpg.vgg.mat - 1690
109620.jpg.vgg.mat - 1691
109627.jpg.vgg.mat - 1692
109629.jpg.vgg.mat - 1693
109633.jpg.vgg.mat - 1694
109637.jpg.vgg.mat - 1695
10964.jpg.vgg.mat - 1696
109649.jpg.vgg.mat - 1697
10965.jpg.vgg.mat - 1698
109650.jpg.vgg.mat - 1699
109653.jpg.vgg.mat - 1700
109668.jpg.vgg.mat - 1701
109684.jpg.vgg.mat - 1702
109687.jpg.vgg.mat - 1703
109692.jpg.vgg.mat - 1704
109708.jpg.vgg.mat - 1705
109713.jpg.vgg.mat - 1706
109716.jpg.vgg.mat - 1707
109719.jpg.vgg.mat - 1708
109725.jpg.vgg.mat - 1709
109728.jpg.vgg.mat - 1710
109736.jpg.vgg.mat - 1711
10977.jpg.vgg.mat - 1712
109770.jpg.vgg.mat - 1713
109772.jpg.vgg.mat - 1714
109782.jpg.vgg.mat - 1715
109789.jpg.vgg.mat - 1716
10982.jpg.vgg.mat - 1717
109827.jpg.vgg.mat - 1718
109828.jpg.vgg.mat - 1719
109833.jpg.vgg.mat - 1720
109845.jpg.vgg.mat - 1721
109849.jpg.vgg.mat - 1722
109855.jpg.vgg.mat - 1723
109858.jpg.vgg.mat - 1724
109861.jpg.vgg.mat - 1725
109864.jpg.vgg.ma

...

89894.jpg.vgg.mat - 72411
89896.jpg.vgg.mat - 72412
89898.jpg.vgg.mat - 72413
89900.jpg.vgg.mat - 72414
89905.jpg.vgg.mat - 72415
89907.jpg.vgg.mat - 72416
89908.jpg.vgg.mat - 72417
89918.jpg.vgg.mat - 72418
89919.jpg.vgg.mat - 72419
89923.jpg.vgg.mat - 72420
89926.jpg.vgg.mat - 72421
89933.jpg.vgg.mat - 72422
89935.jpg.vgg.mat - 72423
89936.jpg.vgg.mat - 72424
89942.jpg.vgg.mat - 72425
89943.jpg.vgg.mat - 72426
89944.jpg.vgg.mat - 72427
89955.jpg.vgg.mat - 72428
89957.jpg.vgg.mat - 72429
89961.jpg.vgg.mat - 72430
89966.jpg.vgg.mat - 72431
89967.jpg.vgg.mat - 72432
89970.jpg.vgg.mat - 72433
89974.jpg.vgg.mat - 72434
8998.jpg.vgg.mat - 72435
89988.jpg.vgg.mat - 72436
89989.jpg.vgg.mat - 72437
89990.jpg.vgg.mat - 72438
89999.jpg.vgg.mat - 72439
90008.jpg.vgg.mat - 72440
9001.jpg.vgg.mat - 72441
90013.jpg.vgg.mat - 72442
9002.jpg.vgg.mat - 72443
90023.jpg.vgg.mat - 72444
90024.jpg.vgg.mat - 72445
90034.jpg.vgg.mat - 72446
9004.jpg.vgg.mat - 72447
90045.jpg.vgg.mat - 72448
90057.jpg.vgg.ma

9234.jpg.vgg.mat - 72839
92345.jpg.vgg.mat - 72840
9235.jpg.vgg.mat - 72841
92351.jpg.vgg.mat - 72842
92354.jpg.vgg.mat - 72843
92356.jpg.vgg.mat - 72844
92372.jpg.vgg.mat - 72845
92374.jpg.vgg.mat - 72846
9238.jpg.vgg.mat - 72847
92385.jpg.vgg.mat - 72848
92386.jpg.vgg.mat - 72849
92392.jpg.vgg.mat - 72850
92396.jpg.vgg.mat - 72851
92406.jpg.vgg.mat - 72852
92409.jpg.vgg.mat - 72853
92419.jpg.vgg.mat - 72854
9242.jpg.vgg.mat - 72855
92438.jpg.vgg.mat - 72856
92440.jpg.vgg.mat - 72857
92442.jpg.vgg.mat - 72858
92447.jpg.vgg.mat - 72859
92449.jpg.vgg.mat - 72860
92474.jpg.vgg.mat - 72861
92477.jpg.vgg.mat - 72862
9248.jpg.vgg.mat - 72863
92482.jpg.vgg.mat - 72864
92488.jpg.vgg.mat - 72865
92492.jpg.vgg.mat - 72866
92497.jpg.vgg.mat - 72867
92501.jpg.vgg.mat - 72868
92504.jpg.vgg.mat - 72869
92505.jpg.vgg.mat - 72870
92506.jpg.vgg.mat - 72871
92507.jpg.vgg.mat - 72872
92509.jpg.vgg.mat - 72873
92527.jpg.vgg.mat - 72874
92529.jpg.vgg.mat - 72875
92531.jpg.vgg.mat - 72876
92534.jpg.vgg.mat

94945.jpg.vgg.mat - 73268
94946.jpg.vgg.mat - 73269
94971.jpg.vgg.mat - 73270
94985.jpg.vgg.mat - 73271
94987.jpg.vgg.mat - 73272
94992.jpg.vgg.mat - 73273
95.jpg.vgg.mat - 73274
95002.jpg.vgg.mat - 73275
95005.jpg.vgg.mat - 73276
95007.jpg.vgg.mat - 73277
95020.jpg.vgg.mat - 73278
95026.jpg.vgg.mat - 73279
95029.jpg.vgg.mat - 73280
95052.jpg.vgg.mat - 73281
95056.jpg.vgg.mat - 73282
9507.jpg.vgg.mat - 73283
95076.jpg.vgg.mat - 73284
9508.jpg.vgg.mat - 73285
951.jpg.vgg.mat - 73286
95106.jpg.vgg.mat - 73287
95107.jpg.vgg.mat - 73288
95111.jpg.vgg.mat - 73289
95113.jpg.vgg.mat - 73290
95115.jpg.vgg.mat - 73291
95124.jpg.vgg.mat - 73292
9513.jpg.vgg.mat - 73293
95130.jpg.vgg.mat - 73294
9515.jpg.vgg.mat - 73295
95154.jpg.vgg.mat - 73296
95155.jpg.vgg.mat - 73297
95160.jpg.vgg.mat - 73298
95163.jpg.vgg.mat - 73299
95179.jpg.vgg.mat - 73300
9518.jpg.vgg.mat - 73301
95190.jpg.vgg.mat - 73302
95201.jpg.vgg.mat - 73303
9521.jpg.vgg.mat - 73304
95213.jpg.vgg.mat - 73305
95215.jpg.vgg.mat - 733

9748.jpg.vgg.mat - 73694
97489.jpg.vgg.mat - 73695
97491.jpg.vgg.mat - 73696
97518.jpg.vgg.mat - 73697
97523.jpg.vgg.mat - 73698
97530.jpg.vgg.mat - 73699
97532.jpg.vgg.mat - 73700
97535.jpg.vgg.mat - 73701
97536.jpg.vgg.mat - 73702
97550.jpg.vgg.mat - 73703
97554.jpg.vgg.mat - 73704
97558.jpg.vgg.mat - 73705
97566.jpg.vgg.mat - 73706
97575.jpg.vgg.mat - 73707
97576.jpg.vgg.mat - 73708
97606.jpg.vgg.mat - 73709
97607.jpg.vgg.mat - 73710
97618.jpg.vgg.mat - 73711
97631.jpg.vgg.mat - 73712
97635.jpg.vgg.mat - 73713
97636.jpg.vgg.mat - 73714
97653.jpg.vgg.mat - 73715
97654.jpg.vgg.mat - 73716
97657.jpg.vgg.mat - 73717
97661.jpg.vgg.mat - 73718
97665.jpg.vgg.mat - 73719
97666.jpg.vgg.mat - 73720
97668.jpg.vgg.mat - 73721
97673.jpg.vgg.mat - 73722
97684.jpg.vgg.mat - 73723
97685.jpg.vgg.mat - 73724
97686.jpg.vgg.mat - 73725
97693.jpg.vgg.mat - 73726
97716.jpg.vgg.mat - 73727
97730.jpg.vgg.mat - 73728
97747.jpg.vgg.mat - 73729
97750.jpg.vgg.mat - 73730
97753.jpg.vgg.mat - 73731
97771.jpg.vgg

99869.jpg.vgg.mat - 74111
99899.jpg.vgg.mat - 74112
99911.jpg.vgg.mat - 74113
99912.jpg.vgg.mat - 74114
99915.jpg.vgg.mat - 74115
99917.jpg.vgg.mat - 74116
9992.jpg.vgg.mat - 74117
99929.jpg.vgg.mat - 74118
99930.jpg.vgg.mat - 74119
99933.jpg.vgg.mat - 74120
99935.jpg.vgg.mat - 74121
99937.jpg.vgg.mat - 74122
99939.jpg.vgg.mat - 74123
9994.jpg.vgg.mat - 74124
99943.jpg.vgg.mat - 74125
99948.jpg.vgg.mat - 74126
99953.jpg.vgg.mat - 74127
99960.jpg.vgg.mat - 74128
99962.jpg.vgg.mat - 74129
99966.jpg.vgg.mat - 74130
99968.jpg.vgg.mat - 74131
99973.jpg.vgg.mat - 74132
99976.jpg.vgg.mat - 74133
99984.jpg.vgg.mat - 74134
99987.jpg.vgg.mat - 74135
99988.jpg.vgg.mat - 74136
99997.jpg.vgg.mat - 74137
99998.jpg.vgg.mat - 74138


In [57]:
#filename = 'vgg_multi_svc_model.sav'
#pickle.dump(classifier_3, open(filename, 'wb'))

def verify_correctness(pred1, test_labels, threshold=0):
    cnt=0
    i = 1
    for x, y in zip(pred1, test_labels):
        #x1= np.array(x)
        #y1 = np.array(y)
        #print(x, y)
        #break
        c=0
        for a, b in zip(x[0], y[0]):
            if(a!=b): c+=1
        if c<=threshold:
            cnt+=1
        i = i + 1
    accuracy = cnt/len(test_labels)
    return accuracy

#print(pred_list.shape, label_list.shape)

print("Accuracy score for strict match is ", verify_correctness(pred_list, label_list, 0)*100)
print("Accuracy score for maximum of 1 mistmatch is ", verify_correctness(pred_list, label_list, 1)*100)
print("Accuracy score for maximum of 2 mistmatch is ", verify_correctness(pred_list, label_list, 2)*100)

Accuracy score for strict match is  49.002394893402
Accuracy score for maximum of 1 mistmatch is  52.628048661899996
Accuracy score for maximum of 2 mistmatch is  57.79361510048
